In [1]:
import magellan as mg

DEBUG:Cloud:Log file (/home/johnny/.picloud/cloud.log) opened


In [3]:
mg.init_jvm()

True

In [4]:
# read tables
A = mg.read_csv('Amazon.csv', key='ID')
B = mg.read_csv('BestBuy.csv', key='ID')

In [5]:
A.head(2)

ID  Brand                                               Name Amazon Price  \
0   1   Asus  ASUS X205TA 11.6 Inch Laptop (Intel Atom, 2 GB...      $199.00   
1   2  Other               AmazonBasics 11.6-Inch Laptop Sleeve        $9.99   

  Original Price                                           Features  
0            NaN  Intel Atom 1.33 GHz Processor. 2 GB DDR3 RAM. ...  
1            NaN  Form-fitting sleeve with quick top-loading acc...

In [6]:
B.head(2)

ID Brand                                               Name    Price  \
0   1  Asus  Asus 11.6 Laptop Intel Atom 2GB Memory 32GB Fl...  $189.99   
1   2    HP  HP 15.6 TouchScreen Laptop Intel Core i3 6GB M...  $379.99   

                                         Description  \
0  11.6&#34; Laptop - Intel Atom - 2GB Memory - 3...   
1  15.6&#34; Touch-Screen Laptop - Intel Core i3 ...   

                                            Features  
0  Microsoft Windows 8.1 operating system preinst...  
1  Microsoft Windows 8.1 operating system preinst...

In [7]:
# Blocking - already done and stored in tableC.csv
C = mg.read_csv('candidate_set3.csv', ltable=A, rtable=B)
len(C)

4373

In [ ]:
# Plan

# 1. Sample candidate set --> S
# 2. Label S --> G
# 3. Split G into development set I, and evaluation set J
# 4. Select best learning-based matcher Y, using I 
# 5. Add triggers to Y ---> Z
# 6. Evaluate Z using J

In [8]:
# Sample the candidate set
S = mg.sample_table(C, 450)

In [9]:
help(mg.sample_table)

Help on function sample_table in module magellan.sampler.sampler:

sample_table(table, size, replace=False)
    Sample MTable
    
    Parameters
    ----------
    table : MTable, input table to be sampled
    size : int, number of samples
    replace : boolean, whether sampling should be done with replacement.
            By default, it is set to False.
    
    Returns
    -------
    sampled_table: MTable, sampled table



In [10]:
# Label S
G = mg.label_table(S, 'gold')

In [17]:
#G.to_csv('cs.csv')

True

In [11]:
# For the demo, use pre-labeled data
G = mg.read_csv('cs.csv', ltable=A, rtable=B)
len(G)

395

In [12]:
# Split G into development (I) and evaluation (J)
IJ = mg.train_test_split(G, train_proportion=0.7)
I = IJ['train']
J = IJ['test']

In [13]:
# check the number of tuples in I and J
(len(I), len(J))

(276, 119)

In [ ]:
# Selecting the best learning-based matcher using I

# Plan 

# 1. Create a set of ML-matchers
# 2. Generate features --> feature_table
# 3. Extract feature vectors using I and feature_table
# 4. Select best learning-based matcher using CV
# 5. Debug the selected matcher (and repeat the above steps)

In [14]:
# Create a set of ML-matchers
dt = mg.DTMatcher(name='DecisionTree', random_state=0)
svm = mg.SVMMatcher()
rf = mg.RFMatcher(name='RF', random_state=0)
nb = mg.NBMatcher(name='NB')
lg = mg.LogRegMatcher(name='LogReg')
ln = mg.LinRegMatcher(name='LinReg')

In [15]:
# check names of the matchers
(dt.name, svm.name)

('DecisionTree', 'SVM_23293602877808148441')

In [16]:
# Generate features
feat_table = mg.get_features_for_matching(A, B)

In [17]:
feat_table

feature_name left_attribute right_attribute  \
0                               ID_ID_exm             ID              ID   
1                               ID_ID_anm             ID              ID   
2                               ID_ID_lev             ID              ID   
3             Brand_Brand_jac_qgm_3_qgm_3          Brand           Brand   
4         Brand_Brand_cos_dlm_dc0_dlm_dc0          Brand           Brand   
5         Brand_Brand_jac_dlm_dc0_dlm_dc0          Brand           Brand   
6                         Brand_Brand_mel          Brand           Brand   
7                         Brand_Brand_lev          Brand           Brand   
8                         Brand_Brand_nmw          Brand           Brand   
9                          Brand_Brand_sw          Brand           Brand   
10                        Brand_Brand_swg          Brand           Brand   
11              Name_Name_jac_qgm_3_qgm_3           Name            Name   
12          Name_Name_cos_dlm_dc0_dlm_dc0           Name            Name   
13      Features_Features_jac_qgm_3_qgm_3       Features        Features   
14  Features_Features_cos_dlm_dc0_dlm_dc0       Features        Features   

   left_attr_tokenizer right_attr_tokenizer           simfunction  \
0                 None                 None           exact_match   
1                 None                 None              abs_norm   
2                 None                 None                   lev   
3                qgm_3                qgm_3               jaccard   
4              dlm_dc0              dlm_dc0                cosine   
5              dlm_dc0              dlm_dc0               jaccard   
6                 None                 None           monge_elkan   
7                 None                 None                   lev   
8                 None                 None      needleman_wunsch   
9                 None                 None        smith_waterman   
10                None                 None  smith_waterman_gotoh   
11               qgm_3                qgm_3               jaccard   
12             dlm_dc0              dlm_dc0                cosine   
13               qgm_3                qgm_3               jaccard   
14             dlm_dc0              dlm_dc0                cosine   

                                             function  \
0              <function ID_ID_exm at 0x7fd12fa28a28>   
1              <function ID_ID_anm at 0x7fd12fa28f50>   
2              <function ID_ID_lev at 0x7fd12fa28ed8>   
3   <function Brand_Brand_jac_qgm_3_qgm_3 at 0x7fd...   
4   <function Brand_Brand_cos_dlm_dc0_dlm_dc0 at 0...   
5   <function Brand_Brand_jac_dlm_dc0_dlm_dc0 at 0...   
6        <function Brand_Brand_mel at 0x7fd12fa5e140>   
7        <function Brand_Brand_lev at 0x7fd12fa5e1b8>   
8        <function Brand_Brand_nmw at 0x7fd12fa5e230>   
9         <function Brand_Brand_sw at 0x7fd12fa5e2a8>   
10       <function Brand_Brand_swg at 0x7fd12fa5e320>   
11  <function Name_Name_jac_qgm_3_qgm_3 at 0x7fd12...   
12  <function Name_Name_cos_dlm_dc0_dlm_dc0 at 0x7...   
13  <function Features_Features_jac_qgm_3_qgm_3 at...   
14  <function Features_Features_cos_dlm_dc0_dlm_dc...   

                                      function_source  
0   from magellan.feature.simfunctions import *\nf...  
1   from magellan.feature.simfunctions import *\nf...  
2   from magellan.feature.simfunctions import *\nf...  
3   from magellan.feature.simfunctions import *\nf...  
4   from magellan.feature.simfunctions import *\nf...  
5   from magellan.feature.simfunctions import *\nf...  
6   from magellan.feature.simfunctions import *\nf...  
7   from magellan.feature.simfunctions import *\nf...  
8   from magellan.feature.simfunctions import *\nf...  
9   from magellan.feature.simfunctions import *\nf...  
10  from magellan.feature.simfunctions import *\nf...  
11  from magellan.feature.simfunctions import *\nf...  
12  from magellan.feature.simfunctions import *\nf...  
13  from m

In [18]:
mg._match_s

{'abs_norm': <function magellan.feature.simfunctions.abs_norm>,
 'cosine': <function magellan.feature.simfunctions.cosine>,
 'exact_match': <function magellan.feature.simfunctions.exact_match>,
 'jaccard': <function magellan.feature.simfunctions.jaccard>,
 'jaro': <function magellan.feature.simfunctions.jaro>,
 'jaro_winkler': <function magellan.feature.simfunctions.jaro_winkler>,
 'lev': <function magellan.feature.simfunctions.lev>,
 'monge_elkan': <function magellan.feature.simfunctions.monge_elkan>,
 'needleman_wunsch': <function magellan.feature.simfunctions.needleman_wunsch>,
 'rel_diff': <function magellan.feature.simfunctions.rel_diff>,
 'smith_waterman': <function magellan.feature.simfunctions.smith_waterman>,
 'smith_waterman_gotoh': <function magellan.feature.simfunctions.smith_waterman_gotoh>,
 'soundex': <function magellan.feature.simfunctions.soundex>}

In [19]:
mg._match_t

{'dlm_dc0': <function magellan.feature.tokenizers.tok_delim>,
 'qgm_2': <function magellan.feature.tokenizers.tok_qgram>,
 'qgm_3': <function magellan.feature.tokenizers.tok_qgram>}

In [20]:
mg._match_c['corres']

[('ID', 'ID'), ('Brand', 'Brand'), ('Name', 'Name'), ('Features', 'Features')]

In [89]:
# NOTE:
# For the demo purposes, use only 'venue', 'year' related features to get the best learning-based matcher 
# and use 'title', 'author' related features to write triggers.

In [21]:
# Select 'year' related features
feat_subset_iter1 = feat_table[14:15]

In [22]:
# Get feature vectors
K = mg.extract_feature_vecs(I, feature_table=feat_subset_iter1, attrs_after='gold')

In [23]:
K.head()

_id  ltable.ID  rtable.ID  Features_Features_cos_dlm_dc0_dlm_dc0  gold
0    0       1027       2542                               0.209657     1
1    1       3943       3425                               0.000000     0
2    2       3807       2290                               0.175762     0
3    3       3741       3235                               0.019245     0
4    4        745       4225                               0.000000     0

In [24]:
# impute K
K.fillna(0, inplace=True)

In [25]:
K.head()

_id  ltable.ID  rtable.ID  Features_Features_cos_dlm_dc0_dlm_dc0  gold
0    0       1027       2542                               0.209657     1
1    1       3943       3425                               0.000000     0
2    2       3807       2290                               0.175762     0
3    3       3741       3235                               0.019245     0
4    4        745       4225                               0.000000     0

In [34]:
# select the best ML matcher using CV
result = mg.select_matcher([dt, rf, svm, nb, lg, ln], table=K, 
        exclude_attrs=['_id', 'ltable.ID', 'rtable.ID', 'gold'],
        target_attr='gold', metric='f1', random_state=0) 

In [35]:
result['selected_matcher']

In [36]:
result['cv_stats']

Name  \
0              DecisionTree   
1                        RF   
2  SVM_23293602877808148441   
3                        NB   
4                    LogReg   
5                    LinReg   

                                             Matcher  Num folds    Fold 1  \
0  <magellan.matcher.dtmatcher.DTMatcher object a...          5  0.461538   
1  <magellan.matcher.rfmatcher.RFMatcher object a...          5  0.461538   
2  <magellan.matcher.svmmatcher.SVMMatcher object...          5  0.000000   
3  <magellan.matcher.nbmatcher.NBMatcher object a...          5  0.714286   
4  <magellan.matcher.logregmatcher.LogRegMatcher ...          5  0.000000   
5  <magellan.matcher.linregmatcher.LinRegMatcher ...          5  0.615385   

    Fold 2    Fold 3    Fold 4    Fold 5  Mean score  
0  0.40000  0.500000  0.666667  0.400000    0.485641  
1  0.47619  0.500000  0.705882  0.444444    0.517611  
2  0.00000  0.000000  0.000000  0.000000    0.000000  
3  0.60000  0.666667  0.533333  0.444444    0.591746  
4  0.00000  0.000000  0.000000  0.000000    0.000000  
5  0.50000  0.250000  0.461538  0.285714    0.422527

In [37]:
# Debug random forest

# Split feature vectors to train and test
UV = mg.train_test_split(K, train_proportion=0.5, random_state=0)
U = UV['train']
V = UV['test']

In [38]:
mg.vis_debug_rf(rf, U, V,
      exclude_attrs=['_id', 'ltable.ID', 'rtable.ID', 'gold'],
       target_attr='gold')

In [39]:
# Debug decision tree

# Split feature vectors to train and test
UV = mg.train_test_split(K, train_proportion=0.5, random_state=0)
U = UV['train']
V = UV['test']

In [40]:
mg.vis_debug_dt(dt, U, V,
      exclude_attrs=['_id', 'ltable.ID', 'rtable.ID', 'gold'],
       target_attr='gold')

In [ ]:
# Add a feature for 'venue'
# 1. create a feature
# 2. Add the feature to feature table.

In [106]:
#feature = mg.get_feature_fn("ltuple['Amazon Price']-rtuple['Price']", mg._match_t, mg._match_s)

In [338]:
# Create a feature
#feature = mg.get_feature_fn("lev(ltuple['Name'], rtuple['Name'])", mg._match_t, mg._match_s)

In [342]:
# Add feature to feature table
#mg.add_feature(feat_table, 'name_lev', feature)

True

In [41]:
feat_table

feature_name left_attribute right_attribute  \
0                               ID_ID_exm             ID              ID   
1                               ID_ID_anm             ID              ID   
2                               ID_ID_lev             ID              ID   
3             Brand_Brand_jac_qgm_3_qgm_3          Brand           Brand   
4         Brand_Brand_cos_dlm_dc0_dlm_dc0          Brand           Brand   
5         Brand_Brand_jac_dlm_dc0_dlm_dc0          Brand           Brand   
6                         Brand_Brand_mel          Brand           Brand   
7                         Brand_Brand_lev          Brand           Brand   
8                         Brand_Brand_nmw          Brand           Brand   
9                          Brand_Brand_sw          Brand           Brand   
10                        Brand_Brand_swg          Brand           Brand   
11              Name_Name_jac_qgm_3_qgm_3           Name            Name   
12          Name_Name_cos_dlm_dc0_dlm_dc0           Name            Name   
13      Features_Features_jac_qgm_3_qgm_3       Features        Features   
14  Features_Features_cos_dlm_dc0_dlm_dc0       Features        Features   

   left_attr_tokenizer right_attr_tokenizer           simfunction  \
0                 None                 None           exact_match   
1                 None                 None              abs_norm   
2                 None                 None                   lev   
3                qgm_3                qgm_3               jaccard   
4              dlm_dc0              dlm_dc0                cosine   
5              dlm_dc0              dlm_dc0               jaccard   
6                 None                 None           monge_elkan   
7                 None                 None                   lev   
8                 None                 None      needleman_wunsch   
9                 None                 None        smith_waterman   
10                None                 None  smith_waterman_gotoh   
11               qgm_3                qgm_3               jaccard   
12             dlm_dc0              dlm_dc0                cosine   
13               qgm_3                qgm_3               jaccard   
14             dlm_dc0              dlm_dc0                cosine   

                                             function  \
0              <function ID_ID_exm at 0x7fd12fa28a28>   
1              <function ID_ID_anm at 0x7fd12fa28f50>   
2              <function ID_ID_lev at 0x7fd12fa28ed8>   
3   <function Brand_Brand_jac_qgm_3_qgm_3 at 0x7fd...   
4   <function Brand_Brand_cos_dlm_dc0_dlm_dc0 at 0...   
5   <function Brand_Brand_jac_dlm_dc0_dlm_dc0 at 0...   
6        <function Brand_Brand_mel at 0x7fd12fa5e140>   
7        <function Brand_Brand_lev at 0x7fd12fa5e1b8>   
8        <function Brand_Brand_nmw at 0x7fd12fa5e230>   
9         <function Brand_Brand_sw at 0x7fd12fa5e2a8>   
10       <function Brand_Brand_swg at 0x7fd12fa5e320>   
11  <function Name_Name_jac_qgm_3_qgm_3 at 0x7fd12...   
12  <function Name_Name_cos_dlm_dc0_dlm_dc0 at 0x7...   
13  <function Features_Features_jac_qgm_3_qgm_3 at...   
14  <function Features_Features_cos_dlm_dc0_dlm_dc...   

                                      function_source  
0   from magellan.feature.simfunctions import *\nf...  
1   from magellan.feature.simfunctions import *\nf...  
2   from magellan.feature.simfunctions import *\nf...  
3   from magellan.feature.simfunctions import *\nf...  
4   from magellan.feature.simfunctions import *\nf...  
5   from magellan.feature.simfunctions import *\nf...  
6   from magellan.feature.simfunctions import *\nf...  
7   from magellan.feature.simfunctions import *\nf...  
8   from magellan.feature.simfunctions import *\nf...  
9   from magellan.feature.simfunctions import *\nf...  
10  from magellan.feature.simfunctions import *\nf...  
11  from magellan.feature.simfunctions import *\nf...  
12  from magellan.feature.simfunctions import *\nf...  
13  from m

In [42]:
# Select 'year'  + 'venue' related features
feat_subset_iter2 = feat_table[13:15]

In [43]:
feat_subset_iter2

feature_name left_attribute right_attribute  \
13      Features_Features_jac_qgm_3_qgm_3       Features        Features   
14  Features_Features_cos_dlm_dc0_dlm_dc0       Features        Features   

   left_attr_tokenizer right_attr_tokenizer simfunction  \
13               qgm_3                qgm_3     jaccard   
14             dlm_dc0              dlm_dc0      cosine   

                                             function  \
13  <function Features_Features_jac_qgm_3_qgm_3 at...   
14  <function Features_Features_cos_dlm_dc0_dlm_dc...   

                                      function_source  
13  from magellan.feature.simfunctions import *\nf...  
14  from magellan.feature.simfunctions import *\nf...

In [44]:
# Get new set of features
K = mg.extract_feature_vecs(I, feature_table=feat_subset_iter2, attrs_after='gold')
# impute K
K.fillna(0, inplace=True)


In [45]:
# Split feature vectors into U and V
UV = mg.train_test_split(K, train_proportion=0.5, random_state=0)
U = UV['train']
V = UV['test']

In [112]:
# Check whether the added features improves the accuracy in the test set.
# Steps
# 1. Train DT using U
# 2. Predict V using DT
# 3. Evaluate predictions


In [367]:
# Train dt using U
dt.fit(table=U, 
       exclude_attrs=['_id', 'ltable.ID', 'rtable.ID', 'gold'], 
       target_attr='gold')

In [46]:
# Train dt using U
nb.fit(table=U, 
       exclude_attrs=['_id', 'ltable.ID', 'rtable.ID', 'gold'], 
       target_attr='gold')

In [47]:
P = nb.predict(table=V, exclude_attrs=['_id', 'ltable.ID', 'rtable.ID', 'gold'], 
              append=True, target_attr='predicted', inplace=False)

In [293]:
# Train rf using U
rf.fit(table=U, 
       exclude_attrs=['_id', 'ltable.ID', 'rtable.ID', 'gold'], 
       target_attr='gold')

In [294]:
# Predict V using dt
P = rf.predict(table=V, exclude_attrs=['_id', 'ltable.ID', 'rtable.ID', 'gold'], 
              append=True, target_attr='predicted', inplace=False)

In [139]:
# Predict V using dt
P = dt.predict(table=V, exclude_attrs=['_id', 'ltable.ID', 'rtable.ID', 'gold'], 
              append=True, target_attr='predicted', inplace=False)

In [48]:
# Evaluate the predictions
eval_result = mg.eval_matches(P, 'gold', 'predicted')
mg.print_eval_summary(eval_result)


Precision : 83.33% (15/18)
Recall : 65.22% (15/23)
F1 : 73.17%
False positives : 3 (out of 18 positive predictions)
False negatives : 8 (out of 120 negative predictions)


In [67]:
# Apply cross validation to find if there is a better matcher
result = mg.select_matcher([dt, rf, svm, nb, lg, ln], table=K, 
        exclude_attrs=['_id', 'ltable.id', 'rtable.id', 'gold'],
        target_attr='gold', metric='recall') 

In [68]:
result['cv_stats']

Name  \
0              DecisionTree   
1                        RF   
2  SVM_23293602877808148441   
3                        NB   
4                    LogReg   
5                    LinReg   

                                             Matcher  Num folds    Fold 1  \
0  <magellan.matcher.dtmatcher.DTMatcher object a...          5  0.500000   
1  <magellan.matcher.rfmatcher.RFMatcher object a...          5  0.714286   
2  <magellan.matcher.svmmatcher.SVMMatcher object...          5  0.000000   
3  <magellan.matcher.nbmatcher.NBMatcher object a...          5  0.666667   
4  <magellan.matcher.logregmatcher.LogRegMatcher ...          5  0.000000   
5  <magellan.matcher.linregmatcher.LinRegMatcher ...          5  0.500000   

     Fold 2    Fold 3    Fold 4    Fold 5  Mean score  
0  0.444444  0.444444  0.700000  0.428571    0.503492  
1  0.533333  0.571429  0.800000  0.285714    0.580952  
2  0.000000  0.000000  0.000000  0.000000    0.000000  
3  0.583333  0.571429  0.800000  0.833333    0.690952  
4  0.000000  0.000000  0.000000  0.000000    0.000000  
5  0.200000  0.333333  0.363636  0.400000    0.359394

In [ ]:
# Select DT as the best matcher -- Y
# Use year + venue related features

In [ ]:
# Add triggers on top of Y

# 1. Split K into U and V
# 2. Use U,V  + Y to write triggers (examine fp, fn).


In [51]:
# Split feature vectors to U and V
UV = mg.train_test_split(K, train_proportion=0.5, random_state=0)
U = UV['train']
V = UV['test']

In [52]:
# Invoke debug interface to check FP and FN
mg.vis_debug_dt(dt, U, V, 
        exclude_attrs=['_id', 'ltable.ID', 'rtable.ID', 'gold'],
        target_attr='gold')

In [83]:
# Add trigger - target false positives: use title related feature
neg_trigger = mg.MatchTrigger()
neg_trigger.add_cond_rule('Name_Name_jac_qgm_3_qgm_3(ltuple, rtuple) < 0.2', feat_table)
neg_trigger.add_cond_status(True)
neg_trigger.add_action(0)

True

In [ ]:
# Check whether the added trigger improves the accuracy in the test set.
# Steps
# 1. Train DT using U
# 2. Predict V using DT
# 3. Apply trigger
# 4. Evaluate the result

In [84]:
nb.fit(table=U, 
       exclude_attrs=['_id', 'ltable.ID', 'rtable.ID', 'gold'], 
       target_attr='gold')

In [85]:
P =nb.predict(table=V, exclude_attrs=['_id', 'ltable.ID', 'rtable.ID', 'gold'], 
              append=True, target_attr='predicted', inplace=False)

In [321]:
rf.fit(table=U, 
       exclude_attrs=['_id', 'ltable.ID', 'rtable.ID', 'gold'], 
       target_attr='gold')

In [322]:
P = rf.predict(table=V, exclude_attrs=['_id', 'ltable.ID', 'rtable.ID', 'gold'], 
              append=True, target_attr='predicted', inplace=False)

In [86]:
# Apply trigger
Q = neg_trigger.execute(P, 'predicted', inplace=False)

In [87]:
# Evaluate the result
eval_result = mg.eval_matches(Q, 'gold', 'predicted')
mg.print_eval_summary(eval_result)

Precision : 100.0% (13/13)
Recall : 56.52% (13/23)
F1 : 72.22%
False positives : 0 (out of 13 positive predictions)
False negatives : 10 (out of 125 negative predictions)


In [88]:
# Do cross-validation for matcher + trigger using I (K)
result = mg.cv_matcher_and_trigger(nb, neg_trigger, table = K, 
                                   exclude_attrs=['_id', 'ltable.id', 'rtable.id', 'gold'],
                                  target_attr='gold')


0%  100%
[#####] | ETA[sec]: 0.000 
Total time elapsed: 0.341 sec


In [89]:
result['cv_stats']

Metric  Num folds    Fold 1  Fold 2  Fold 3    Fold 4    Fold 5  \
0  precision          5  0.750000    1.00    1.00  1.000000  1.000000   
1     recall          5  0.666667    0.60    0.25  0.428571  0.500000   
2         f1          5  0.705882    0.75    0.40  0.600000  0.666667   

   Mean score  
0    0.950000  
1    0.489048  
2    0.624510

In [90]:
# Recall the cv for just the matcher (without trigger) was
result = mg.cv_matcher_and_trigger(nb, [], table = K, 
                                   exclude_attrs=['_id', 'ltable.id', 'rtable.id', 'gold'],
                                  target_attr='gold')

0%  100%
[#####] | ETA[sec]: 0.000 
Total time elapsed: 0.156 sec


In [91]:
result['cv_stats']

Metric  Num folds    Fold 1    Fold 2    Fold 3    Fold 4    Fold 5  \
0  precision          5  0.600000  0.714286  0.555556  1.000000  0.750000   
1     recall          5  0.750000  0.833333  0.500000  0.428571  0.900000   
2         f1          5  0.666667  0.769231  0.526316  0.600000  0.818182   

   Mean score  
0    0.723968  
1    0.682381  
2    0.676079

In [ ]:
# Now Z is DT (features: feat_subset_iter2) + neg_trigger
# Validate Z using J
# Steps
# 1. Extract feature vectors (using feat_subset_iter2) -- > M
# 2. Train DT using H (feature vectors generated using I)
# 3. Predict M using DT
# 4. Apply negative trigger
# 5. Evaluate the result

In [92]:
# Extract feature vectors
M = mg.extract_feature_vecs(J, feature_table=feat_subset_iter2, attrs_after='gold')

In [93]:
# Impute missing values
M.fillna(0, inplace=True)

In [109]:
# Train using feature vectors from I 
ln.fit(table=K, 
       exclude_attrs=['_id', 'ltable.ID', 'rtable.ID', 'gold'], 
       target_attr='gold')

In [110]:
P =ln.predict(table=M, exclude_attrs=['_id', 'ltable.ID', 'rtable.ID', 'gold'], 
              append=True, target_attr='predicted', inplace=False)

In [111]:
# Evaluate the result
eval_result = mg.eval_matches(P, 'gold', 'predicted')
mg.print_eval_summary(eval_result)

Precision : 87.5% (7/8)
Recall : 41.18% (7/17)
F1 : 56.0%
False positives : 1 (out of 8 positive predictions)
False negatives : 10 (out of 111 negative predictions)


In [ ]:
eval_result = mg.eval_matches(T, 'gold', 'predicted')
mg.print_eval_summary(eval_result)

In [112]:
# Predict M 
N = nb.predict(table=M, exclude_attrs=['_id', 'ltable.ID', 'rtable.ID', 'gold'], 
              append=True, target_attr='predicted', inplace=False)

In [113]:
# Apply trigger
T = neg_trigger.execute(N, 'predicted', inplace=False)

In [114]:
# Evaluate the result
eval_result = mg.eval_matches(T, 'gold', 'predicted')
mg.print_eval_summary(eval_result)


Precision : 100.0% (11/11)
Recall : 64.71% (11/17)
F1 : 78.57%
False positives : 0 (out of 11 positive predictions)
False negatives : 6 (out of 108 negative predictions)


In [ ]:
T.to_csv('final_matches.csv')